---

# S03E06 : Fonctions & décorateurs - Décorateur avancés

Cyril Desjouy

---

Comme vous l'avez constaté précédemment, l'utilisation d'un décorateur est un moyen simple et efficace de factoriser du code et de facilité sa réutilisation. Dans ce notebook, nous allons poursuivre la découverte de ce type de fonctions à travers quelques recettes permettant de créer des décorateurs :

* prenant eux mêmes des arguments d'entrée,
* gardant trace de leur état grâce aux attributs de fonctions,
* ajoutant des arguments d'entrée à la fonction ***wrapper***.

Vous l'aurez compris, cette liste n'est pas exhaustive, et les possibilités proposées par les décorateurs sont infinies!


## 1. Décorateurs avec arguments

Il arrive souvent qu'il soit nécessaire de passer un ou des argument(s) d'entrée à un décorateur afin de personnaliser la manière dont la décoration est faite. Dans ce cas, on entoure généralement le décorateur et son ***wrapper*** par une fonction additionnelle dont l'objectif est de gérer les arguments. 

L'exemple suivant nous servira de base pour comprendre les mécanismes mis en jeu lors de la création de décorateur avec argument d'entrée:

In [18]:
import functools

def fancy(char='*', n=80):
    def decorator(func):
        @functools.wraps(func)
        def wrapper(*args, **kwargs):
            print(n*char + f'\nExecuting {func.__name__}')
            value = func(*args, **kwargs)
            print(f'Output:{value}\n' + n*char)
            return value
        return wrapper
    return decorator

@fancy('*')
def multiply(x, y):
    return x*y

results = multiply(2, 3)

********************************************************************************
Executing multiply
Output:6
********************************************************************************


* La fonction centrale `wrapper` n'est pas très différente de celles que nous avons vu précédemment. Les variables `n` et `char` sont trouvées par l'interpréteur dans un ***scope*** supérieur, celui de `fancy` qui est un ***enclosed scope***.
* La fonction `decorator` est exactement la même que celle vues précédemment. Elle prend la fonction `func` en argument d'entrée et retourne une référence au `wrapper`.
* La fonction `fancy` n'est qu'une couche supplémentaire permettant de récupérer les arguments d'entrée qui seront rendus disponibles dans les ***scopes*** inférieurs. Cette fonction retourne une référence au `decorator`.
* L'utilisation du décorateur `@fancy` se fait maintenant avec des `( )` (et des éventuels arguments d'entrée). Dans les exemples précédents les décorateurs étaient utilisés sans parenthèses pour faire référence à la fonction de décoration. Dans le cas présent, pour faire référence à la fonction de décoration, il est nécessaire d'appeler la fonction `fancy` **avec** ses arguments d'entrée. 
* Les variables `char` et `n` sont passées aux ***scopes*** inférieurs. Une ***closure*** est alors créée.

Si le décorateur est appelé sans arguments, une exception est levée. Comme précisé ci-dessus, il est absolument nécessaire que la fonction `fancy` soit **appelée** pour retourner la référence à `decorator`.

Il est cependant possible de créer des décorateurs qui peuvent être utilisés avec ou sans arguments.

<div class="alert alert-block alert-info">
Testez l'exemple suivant en modifiant <code>@fancy</code>. 
</div>

In [15]:
import functools

def fancy(func=None, char='*', n=80):
    def decorator(func):
        @functools.wraps(func)
        def wrapper(*args, **kwargs):
            print(n*char + f'\nExecuting {func.__name__}')
            value = func(*args, **kwargs)
            print(f'Output:{value}\n' + n*char)
            return value
        return wrapper
    
    if func:
        return decorator(func)
    
    return decorator

@fancy
def multiply(x, y):
    return x*y

results = multiply(2, 3)



********************************************************************************
Executing multiply
Output:6
********************************************************************************


La fonction `fancy` prend alors la fonction à décorer en argument d'entrée optionnel (`function`). 
Si cet argument est fourni, `fancy` **appelle** `decorator`. Si elle n'est pas fournie, il retourne juste une **référence** à `decorator`. Il est ainsi possible d'utiliser `@fancy` avec ou sans parenthèse!

Notez qu'une excellente écriture alternative utilisant des ***partials functions*** est proposée dans le *[Python cookbook](https://d.cxcore.net/Python/Python_Cookbook_3rd_Edition.pdf)* (Recipe 9.6):

In [56]:
def fancy(func=None, char='*', n=80):
    
    if func is None:
         return functools.partial(fancy, char=char, n=n)

    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        print(n*char + f'\nExecuting {func.__name__}')
        value = func(*args, **kwargs)
        print(f'Output:{value}\n' + n*char)
        return value
    
    return wrapper

@fancy(char='-', n=20)
def multiply(x, y):
    return x*y

results = multiply(2, 3)

--------------------
Executing multiply
Output:6
--------------------


## 2. Décorateur gardant trace de son état

Les fonctions, comme tout objet sous Python, possède des attributs. Il est possible de créer un nouvel attribut de fonction comme suit:
```python
def func():
    pass

func.attribute = 'attribute'
print(func.attribute)        # display 'attribute'
```

Pour aller plus loin, il est également possible d'agir sur cet attribut depuis la fonction:
```python
def counter():
    counter.count += 1
    print(counter.count)
    
counter.count = 0 
```

```python
>> counter()
1
>> counter()
2
>> counter()
3
...
```
Gardez juste en mémoire que ces attributs de fonctions sont initialisés en dehors de la fonction. Il peuvent ensuite être modifiés dans la fonction. Ce mécanisme permet de créer facilement des décorateurs gardant trace d'un état. Par exemple:


In [23]:
import functools

def count(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        wrapper.calls += 1
        print(f"Call {wrapper.calls} of {func.__name__!r} function")
        return func(*args, **kwargs)
    wrapper.calls = 0
    return wrapper

@count
def hello():
    print("Hello world!")
    
for i in range(3):
    hello()

Call 1 of 'hello' function
Hello world!
Call 2 of 'hello' function
Hello world!
Call 3 of 'hello' function
Hello world!


## 3. Décorateur ajoutant des arguments 

Il est tout à fait possible de créer un décorateur permettant d'ajouter un argument optionnel à la fonction à décorer. Pour ce faire, il suffit d'ajouter cet argument directement à `wrapper`:

In [36]:
import functools

def verbose(func):    
    @functools.wraps(func)
    def wrapper(*args, level=0, **kwargs):
        if level == 1:
            print(f'Calling {func.__name__}')
        if level == 2:
            print(f'Calling {func.__name__} with')
            print(f'\t* {str(args)} as positional arguments')
            print(f'\t* {str(kwargs)} as keyword arguments')
        return func(*args, **kwargs)
    return wrapper

@verbose
def stuff(task, like_a=''):
    print(f'Doing {task} like a {like_a}'.center(80))

print('Without argument level:')
stuff('Python', like_a='boss')

print('\nWith argument level:')
stuff('Python', like_a='boss', level=2)

Without argument level:
                            Doing Python like a boss                            

With argument level:
Calling stuff with
	* ('Python',) as positional arguments
	* {'like_a': 'boss'} as keyword arguments
                            Doing Python like a boss                            


## Application

<div class="alert alert-block alert-info">
Écrire un décorateur permettant de mesurer le temps qu'une fonction met à s'exécuter. 
Le décorateur gardera en mémoire une trace de tous les temps mesurés. Le décorateur fonctionnera comme suit s'il est utilisé sans argument d'entrée:
</div>

```python
@timing
def mult(x, y):
    return x*y

>> m1 = mult(2, 4)
>> m2 = mult(2, 4)
>> print(mult.log)
{}
```
<div class="alert alert-block alert-info">
et comme suit s'il est utilisé avec l'argument <code>log</code> valant <code>True</code>
</div>


```python
@timing(log=True)
def mult(x, y):
    return x*y

>> m1 = mult(2, 4)
>> m2 = mult(2, 4)
>> print(mult.log)
{'mult1': 2.843968104571104e-06, 'mult2': 1.5129917301237583e-06}
```

## Bibliographie

* [Python Cookbook - Recipe 9.6](https://d.cxcore.net/Python/Python_Cookbook_3rd_Edition.pdf)
* [Real Python - Primer on Python decorators](https://realpython.com/primer-on-python-decorators/)